In [1]:
import numpy as np
import ctrl, electric
from bokeh.io import output_notebook, show
from bokeh.plotting import figure
from bokeh.layouts import gridplot
from bokeh.models import ColumnDataSource, HoverTool, CustomJS
output_notebook()


Loading BokehJS ...

In [2]:
T = np.linspace(0.0,0.04,400)

## Balanced system

In [3]:
V_peak = 400.0*np.sqrt(2.0/3.0)
V_a = V_peak*np.exp(1j*np.deg2rad(0.0))   
V_b = V_peak*np.exp(1j*np.deg2rad(-120.0))   
V_c = V_peak*np.exp(1j*np.deg2rad(-240.0)) 

In [4]:
V_p = np.array([[V_a],[V_b],[V_c]]) # peak values
V = V_p/np.sqrt(2.0)

In [5]:
I_peak = 150.0*np.sqrt(2.0)
pf = 1.0 # power factor
phi = np.arccos(pf)
I_a = I_peak*np.exp(1j*(np.deg2rad(0.0)-phi))   
I_b = I_peak*np.exp(1j*(np.deg2rad(-120.0)-phi))  
I_c = I_peak*np.exp(1j*(np.deg2rad(-240.0)-phi)) 

In [6]:
I_p = np.array([[I_a],[I_b],[I_c]]) # peak values
I = I_p/np.sqrt(2.0)

In [7]:
v_abc = electric.ph2inst(V_p,T)
i_abc = electric.ph2inst(I_p,T)

In [8]:
fig = figure(width=600, height=300)
decim = 1
fig.line(T[0:-1:decim],v_abc[0,0:-1:decim], line_width=1, color='red')
fig.line(T[0:-1:decim],v_abc[1,0:-1:decim], line_width=1, color='green')    
fig.line(T[0:-1:decim],v_abc[2,0:-1:decim], line_width=1, color='blue')  

fig.line(T[0:-1:decim],i_abc[0,0:-1:decim], line_width=1, color='red')
fig.line(T[0:-1:decim],i_abc[1,0:-1:decim], line_width=1, color='green')    
fig.line(T[0:-1:decim],i_abc[2,0:-1:decim], line_width=1, color='blue')

show(fig)

In [9]:
p = v_abc*i_abc
p_total = np.sum(p,axis=0)

In [10]:
fig = figure(width=600, height=300)
fig.line(T,p[0]/1000, line_width=2, color='red')
fig.line(T,p[1]/1000, line_width=2, color='green')    
fig.line(T,p[2]/1000, line_width=2, color='blue')  
fig.line(T,p_total/1000, line_width=2, color='magenta')
show(fig)

In [11]:
S_3ph = V*np.conj(I)
P_3ph = S_3ph.real
Q_3ph = S_3ph.imag

In [12]:
np.sum(S_3ph)

(103923.04845413262+0j)

In [13]:
S_3ph

array([[ 34641.01615138 +0.00000000e+00j],
       [ 34641.01615138 +3.63797881e-12j],
       [ 34641.01615138 -3.63797881e-12j]])

In [14]:
P_3ph

array([[ 34641.01615138],
       [ 34641.01615138],
       [ 34641.01615138]])

## Unbalanced currents

In [15]:
T = np.linspace(0.0,0.04,4000)

In [16]:
# https://en.wikipedia.org/wiki/Symmetrical_components
alpha = np.exp(1j*2.0/3.0*np.pi)

fortescue  = np.array([[1,1,1],[1,alpha**2,alpha],[1,alpha,alpha**2]])
ifortescue = 1.0/3.0*np.array([[1,1,1],[1,alpha,alpha**2],[1,alpha**2,alpha]])

In [17]:
I_peak = 150.0*np.sqrt(2.0)
pf = 0.8 # power factor
phi = np.arccos(pf)
I_a = I_peak*np.exp(1j*(np.deg2rad(0.0)-phi))   
I_b = I_peak*np.exp(1j*(np.deg2rad(-120.0)-phi))  
I_c = 0.8*I_peak*np.exp(1j*(np.deg2rad(-240.0)-phi)) 

I_p = np.array([[I_a],[I_b],[I_c]]) # peak values
I = I_p/np.sqrt(2.0)

In [18]:
I_012 = ifortescue @ I

In [19]:
I_012

array([[  -1.19615242 -9.92820323j],
       [ 112.00000000-84.j        ],
       [   9.19615242 +3.92820323j]])

In [20]:
v_abc = electric.ph2inst(V_p,T)
i_abc = electric.ph2inst(I_p,T)

In [21]:
fig = figure(width=600, height=300)
decim = 1
fig.line(T[0:-1:decim],v_abc[0,0:-1:decim], line_width=2, color='red')
fig.line(T[0:-1:decim],v_abc[1,0:-1:decim], line_width=2, color='green')    
fig.line(T[0:-1:decim],v_abc[2,0:-1:decim], line_width=2, color='blue')  

fig.line(T[0:-1:decim],i_abc[0,0:-1:decim], line_width=2, color='red')
fig.line(T[0:-1:decim],i_abc[1,0:-1:decim], line_width=2, color='green')    
fig.line(T[0:-1:decim],i_abc[2,0:-1:decim], line_width=2, color='blue')

show(fig)

In [22]:
p = v_abc*i_abc
p_total = np.sum(p,axis=0)

In [23]:
fig = figure(width=600, height=300)
fig.line(T,p[0]/1000, line_width=2, color='red')
fig.line(T,p[1]/1000, line_width=2, color='green')    
fig.line(T,p[2]/1000, line_width=2, color='blue')  
fig.line(T,p_total/1000, line_width=2, color='magenta')
show(fig)

In [24]:
p_mean = np.trapz(p_total,T)/0.04
print('p_mean = {:2.3f}'.format(p_mean))

p_mean = 77595.876


In [25]:
I_012 = ifortescue @ I
V_012 = ifortescue @ V

In [26]:
np.sum(3*V_012 * np.conj(I_012))

(77595.876179085695+58196.90713431425j)

In [27]:
V_peak = 400.0*np.sqrt(2.0/3.0)
V_a = V_peak*np.exp(1j*np.deg2rad(0.0))   
V_b = V_peak*np.exp(1j*np.deg2rad(-120.0))   
V_c = V_peak/0.8*np.exp(1j*np.deg2rad(-240.0)) 
V_p = np.array([[V_a],[V_b],[V_c]]) # peak values
V = V_p/np.sqrt(2.0)

In [28]:
v_abc = electric.ph2inst(V_p,T)
i_abc = electric.ph2inst(I_p,T)

In [29]:
p = v_abc*i_abc
p_total = np.sum(p,axis=0)
p_total

array([ 83138.43876331,  83138.43876331,  83138.43876331, ...,
        83138.43876331,  83138.43876331,  83138.43876331])

In [30]:
fig = figure(width=600, height=300)
fig.line(T,p[0]/1000, line_width=2, color='red')
fig.line(T,p[1]/1000, line_width=2, color='green')    
fig.line(T,p[2]/1000, line_width=2, color='blue')  
fig.line(T,p_total/1000, line_width=2, color='magenta')
show(fig)

In [31]:
I_012 = ifortescue @ I
V_012 = ifortescue @ V

In [32]:
np.abs(V_012)

array([[  19.24500897],
       [ 250.18511665],
       [  19.24500897]])

In [33]:
np.abs(I_012)

array([[  10.],
       [ 140.],
       [  10.]])

In [34]:
250/140

1.7857142857142858

In [35]:
19.24/10

1.924

In [36]:
np.sum(V_012*I_012)

(28174.69313645373-21131.019852340291j)

In [37]:
import ctrl


In [38]:
v_dq0 = ctrl.clark(v_abc)
i_dq0 = ctrl.clark(i_abc)

In [39]:
fig = figure(width=600, height=300)
decim = 1
fig.line(T[0:-1:decim],v_dq0[0,0:-1:decim], line_width=2, color='red')
fig.line(T[0:-1:decim],v_dq0[1,0:-1:decim], line_width=2, color='green')    
fig.line(T[0:-1:decim],v_dq0[2,0:-1:decim], line_width=2, color='blue')  

fig.line(T[0:-1:decim],i_dq0[0,0:-1:decim], line_width=2, color='red', line_dash = 'dashed')
fig.line(T[0:-1:decim],i_dq0[1,0:-1:decim], line_width=2, color='green', line_dash = 'dashed')    
fig.line(T[0:-1:decim],i_dq0[2,0:-1:decim], line_width=2, color='blue', line_dash = 'dashed')

show(fig)

In [48]:
v_dq_p = ctrl.park2(v_abc,T,2.0*np.pi*50)
i_dq_p = ctrl.park2(i_abc,T,2.0*np.pi*50)
v_dq_m = ctrl.park2(v_abc,T,-2.0*np.pi*50)
i_dq_m = ctrl.park2(i_abc,T,-2.0*np.pi*50)

In [56]:
fig = figure(width=600, height=300)
decim = 1
fig.line(T[0:-1:decim],v_dq_p[0,0:-1:decim].real, line_width=2, color='red')
fig.line(T[0:-1:decim],v_dq_p[1,0:-1:decim].real, line_width=2, color='green')    

fig.line(T[0:-1:decim],i_dq_p[0,0:-1:decim].real, line_width=2, color='red', line_dash = 'dashed')
fig.line(T[0:-1:decim],i_dq_p[1,0:-1:decim].real, line_width=2, color='green', line_dash = 'dashed')    

show(fig)

In [59]:
fig = figure(width=600, height=300)
decim = 1
fig.line(T[0:-1:decim],v_dq_m[0,0:-1:decim].real, line_width=2, color='red')
fig.line(T[0:-1:decim],v_dq_m[1,0:-1:decim].real, line_width=2, color='green')    

fig.line(T[0:-1:decim],i_dq_m[0,0:-1:decim].real, line_width=2, color='red', line_dash = 'dashed')
fig.line(T[0:-1:decim],i_dq_m[1,0:-1:decim].real, line_width=2, color='green', line_dash = 'dashed')    

show(fig)

In [58]:
np.mean(v_dq_p.real,axis=1)

array([  3.53811783e+02,  -5.89255651e-03])

In [57]:
np.mean(v_dq_m.real,axis=1)

array([-13.51982255, -23.57022604])